<a href="https://colab.research.google.com/github/learnvisionAI/ObjectDetection_YOLO/blob/main/Session4_YOLOV8_ObjectTracking/Object_tracking_working.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install ultralytics

import ultralytics
ultralytics.__version__

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 663.2/663.2 kB 3.1 MB/s eta 0:00:00


'8.0.230'

In [ ]:
import torch

torch.cuda.is_available()

True

In [ ]:
from ultralytics import YOLO

# Configure the tracking parameters and run the tracker
model = YOLO('yolov8m.pt')



100%|██████████| 49.7M/49.7M [00:00<00:00, 201MB/s]


In [ ]:
results = model.track(source="/content/people.mp4",conf=0.3, iou=0.5, save=True, tracker="bytetrack.yaml")

requirements: Ultralytics requirement ['lapx>=0.5.2'] not found, attempting AutoUpdate...
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 9.9 MB/s eta 0:00:00

requirements: AutoUpdate success ✅ 6.3s, installed 1 package: ['lapx>=0.5.2']
requirements: ⚠️ Restart runtime or rerun command for updates to take effect



WARNING ⚠️ inference results will accumulate in RAM unless `stream=True` is passed, causing potential out-of-memory
errors for large sources or long-running streams and videos. See https://docs.ultralytics.com/modes/predict/ for help.

Example:
    results = model(source=..., stream=True)  # generator of Results objects
    for r in results:
        boxes = r.boxes  # Boxes object for bbox outputs
        masks = r.masks  # Masks object for segment masks outputs
        probs = r.probs  # Class probabilities for classification outputs

WARNING ⚠️ NMS time limit 0.550s exceeded
video 1/1 (1/341) /content/people.mp4: 384x640 11 persons, 86.0ms
video 1/1 (2/341) /cont

## counting

In [2]:
!pip install ultralytics
from ultralytics import YOLO
from ultralytics.solutions import object_counter
import cv2

In [79]:
model = YOLO("yolov8n.pt")
cap = cv2.VideoCapture("/content/people.mp4")
assert cap.isOpened(), "Error reading video file"

In [80]:
# Define region points
# region_points = [(200, 250), (460, 250)]
region_points = [(50, 300), (1260, 300)]

In [81]:
# Video writer
video_writer = cv2.VideoWriter("object_counting_output.avi",
                       cv2.VideoWriter_fourcc(*'mp4v'),
                       int(cap.get(5)),
                       (int(cap.get(3)), int(cap.get(4))))

In [82]:
# Init Object Counter
counter = object_counter.ObjectCounter()
counter.set_args(view_img=True,
                 reg_pts=region_points,
                 classes_names=model.names,
                 draw_tracks=True)

while cap.isOpened():
    success, im0 = cap.read()
    if not success:
        print("Video frame is empty or video processing has been successfully completed.")
        break
    tracks = model.track(im0, persist=True, show=False)

    im0 = counter.start_counting(im0, tracks)
    video_writer.write(im0)

cap.release()
video_writer.release()
cv2.destroyAllWindows()

WARNING ⚠️ Environment does not support cv2.imshow() or PIL Image.show()

Line Counter Initiated.

0: 384x640 12 persons, 2 birds, 22.6ms
Speed: 2.1ms preprocess, 22.6ms inference, 2.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 12 persons, 2 birds, 18.5ms
Speed: 1.9ms preprocess, 18.5ms inference, 2.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 13 persons, 2 birds, 16.3ms
Speed: 1.9ms preprocess, 16.3ms inference, 2.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 13 persons, 2 birds, 10.4ms
Speed: 3.6ms preprocess, 10.4ms inference, 1.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 15 persons, 2 birds, 12.7ms
Speed: 3.6ms preprocess, 12.7ms inference, 1.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 15 persons, 2 birds, 14.4ms
Speed: 2.0ms preprocess, 14.4ms inference, 2.3ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 15 persons, 2 birds, 10.0ms
Speed: 4.1ms preprocess, 10.0ms inferenc

In [28]:
from IPython.display import HTML
from base64 import b64encode
import os

# Input video path
save_path = '/content/object_counting_output.avi'

# Compressed video path
compressed_path = "/content/result_compressed.mp4"

os.system(f"ffmpeg -i {save_path} -vcodec libx264 {compressed_path}")

# Show video
mp4 = open(compressed_path,'rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=400 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)